# 🥇 Camada Gold

Nesta camada **Gold** do pipeline de dados, realizamos a modelagem e construção das principais tabelas dimensionais e fato, consolidando e enriquecendo os dados provenientes das camadas anteriores (Bronze e Silver). O objetivo é fornecer uma base analítica robusta, confiável e otimizada para consultas de negócio, relatórios e análises avançadas. Esta camada representa o estágio mais avançado do pipeline, onde os dados estão prontos para gerar valor ao negócio, suportando decisões estratégicas e operacionais.

## Atividades Realizadas

- **Padronização e Enriquecimento dos Dados:** 
  - As tabelas dimensionais foram criadas a partir de dados tratados e limpos, garantindo unicidade, integridade e enriquecimento das informações relevantes para o negócio.
  - Foram aplicadas regras de negócio para classificação de risco, padronização de nomes e tratamento de valores nulos ou inconsistentes.

- **Criação das Tabelas Dimensionais:**
  - **dim_clientes:** Contém informações únicas dos clientes, como identificadores e prefixos de CEP.
  - **dim_vendedores:** Consolida dados dos vendedores, facilitando análises de performance e localização.
  - **dim_pagamentos:** Estrutura os métodos de pagamento, atribuindo níveis de risco conforme o tipo de transação.
  - **dim_data:** Tabela de calendário detalhada, com informações de data, dia da semana, mês e ano, permitindo análises temporais precisas.
  - **dim_geolocalizacao:** Reúne dados de cidades e geolocalização, filtrando apenas cidades válidas e relevantes para o negócio.
  - **dim_chargebacks:** Detalha os chargebacks, padronizando motivos e respostas, importante para análises de risco e fraudes.

- **Criação da Tabela Fato:**
  - **fato_transacoes:** Consolida todas as transações realizadas, integrando informações de pedidos, clientes, vendedores, pagamentos, valores totais e status dos pedidos. Essa tabela é fundamental para análises de vendas, receitas, comportamento do cliente e eficiência operacional.

- **Otimização para Análises:**
  - As tabelas foram desenhadas para facilitar a integração entre dimensões e fatos, otimizando consultas analíticas e relatórios de BI.
  - Utilização de funções analíticas, agregações e joins eficientes para garantir performance e escalabilidade.

## Benefícios para o Negócio

- **Visão 360º do Processo de Vendas:** Permite análises detalhadas de cada etapa do funil de vendas, desde o cliente até o recebimento do pagamento.
- **Base para Indicadores e Dashboards:** Estrutura pronta para alimentar dashboards, KPIs e análises preditivas.
- **Governança e Qualidade dos Dados:** Garantia de dados confiáveis, auditáveis e prontos para uso por diferentes áreas da empresa.

In [0]:
%sql
USE CATALOG `100cep_gateway`;

In [0]:
%sql
USE SCHEMA gold;

In [0]:
%sql
CREATE OR REPLACE TABLE `100cep_gateway`.gold.dim_clientes AS
WITH clientes AS(
SELECT 
  cliente_id,
  cep_prefixo
FROM `100cep_gateway`.silver.`100cep_clientes`
)
SELECT
  *
FROM 
  clientes

num_affected_rows num_inserted_rows

In [0]:
%sql
CREATE OR REPLACE TABLE `100cep_gateway`.gold.dim_vendedores AS
WITH vendedores AS(
SELECT 
  vendedor_id,
  cep_prefixo
FROM `100cep_gateway`.silver.`100cep_vendedores`
)
SELECT
  *
FROM
  vendedores;

num_affected_rows num_inserted_rows

In [0]:
%sql
CREATE OR REPLACE TABLE dim_data AS
WITH calendario AS (
  SELECT 
    DATE(data_pedido) AS data_calendario,
    DAY(data_pedido) AS dia,
    MONTH(data_pedido) AS mes,
    YEAR(data_pedido) AS ano,
    UPPER(CASE DAYOFWEEK(data_pedido)
      WHEN 1 THEN 'DOMINGO'
      WHEN 2 THEN 'SEGUNDA-FEIRA'
      WHEN 3 THEN 'TERCA-FEIRA'
      WHEN 4 THEN 'QUARTA-FEIRA'
      WHEN 5 THEN 'QUINTA-FEIRA'
      WHEN 6 THEN 'SEXTA-FEIRA'
      WHEN 7 THEN 'SABADO'
    END) AS nome_dia_semana,
    UPPER(CASE MONTH(data_pedido)
      WHEN 1 THEN 'JANEIRO'
      WHEN 2 THEN 'FEVEREIRO'
      WHEN 3 THEN 'MARÇO'
      WHEN 4 THEN 'ABRIL'
      WHEN 5 THEN 'MAIO'
      WHEN 6 THEN 'JUNHO'
      WHEN 7 THEN 'JULHO'
      WHEN 8 THEN 'AGOSTO'
      WHEN 9 THEN 'SETEMBRO'
      WHEN 10 THEN 'OUTUBRO'
      WHEN 11 THEN 'NOVEMBRO'
      WHEN 12 THEN 'DEZEMBRO'
    END) AS nome_mes
  FROM 
    `100cep_gateway`.silver.`100cep_pedidos`
  WHERE 
    data_pedido IS NOT NULL
  GROUP BY 
    DATE(data_pedido),
    DAY(data_pedido),
    MONTH(data_pedido),
    YEAR(data_pedido),
    DAYOFWEEK(data_pedido)
)
SELECT
  *
FROM 
  calendario

num_affected_rows num_inserted_rows

In [0]:
%sql
CREATE OR REPLACE TABLE dim_geolocalizacao AS 
WITH cidades_validas AS (
SELECT
  cidade,
  COUNT(cidade) AS contagens
FROM
  `100cep_gateway`.silver.`100cep_geolocalizacao`
GROUP BY
  cidade
HAVING
  contagens > 1
ORDER BY
  COUNT(cidade) DESC)

SELECT
  cep_prefixo,
  cidade,
  estado,
  latitude,
  longitude
FROM 
  `100cep_gateway`.silver.`100cep_geolocalizacao`
WHERE 
  cidade IN (
    SELECT cidade FROM cidades_validas
    )

num_affected_rows num_inserted_rows

In [0]:
CREATE OR REPLACE TABLE dim_chargebacks AS
WITH chargebacks AS (
SELECT
  pedido_id,
  REPLACE(motivo_chargeback, "_"," ") AS motivo_chargeback,
  status_chargeback,
  resposta_emitente,
  resposta_adquirente
FROM 
  `100cep_gateway`.silver.`100cep_chargebacks`
)
SELECT 
  *
FROM
  chargebacks

num_affected_rows num_inserted_rows

In [0]:
%sql
CREATE OR REPLACE TABLE `100cep_gateway`.gold.fato_transacoes AS
WITH itens_agg AS (
  SELECT
    pedido_id,
    SUM(preco_produto) AS preco_total,
    SUM(valor_frete) AS frete_total
  FROM 100cep_gateway.silver.`100cep_itens_pedidos`
  GROUP BY pedido_id
)

SELECT
  DISTINCT i.pedido_id,
  o.cliente_id,
  v.vendedor_id,
  CAST(o.data_pedido AS DATE) AS data_pedido,
  CONCAT(
    LPAD(HOUR(o.data_pedido), 2, '0'), ':',
    LPAD(MINUTE(o.data_pedido), 2, '0'), ':',
    LPAD(SECOND(o.data_pedido), 2, '0')
  ) AS horario_pedido,
  p.tipo_pagamento,
  CAST(p.valor_transacao AS DECIMAL(12,2)) AS valor_transacao,
  i.preco_total,
  i.frete_total,
  o.status_pedido
FROM itens_agg AS i
LEFT JOIN 100cep_gateway.silver.`100cep_pedidos` AS o
  USING(pedido_id)
LEFT JOIN 100cep_gateway.silver.`100cep_pagamentos` AS p
  USING(pedido_id)
LEFT JOIN 100cep_gateway.silver.`100cep_itens_pedidos` AS v
  USING(pedido_id)
WHERE valor_transacao IS NOT NULL

num_affected_rows num_inserted_rows

In [0]:
SELECT *
FROM `100cep_gateway`.gold.fato_transacoes

pedido_id cliente_id vendedor_id data_pedido horario_pedido tipo_pagamento valor_transacao preco_total frete_total status_pedido 0005f50442cb953dcd1d21e1fb923495 351d3cb2cee3c7fd0af6616c82df21d3 ba143b05f0110f0dc71ad71b4466ce92 2018-07-02 10:59:39 CARTAO DE CREDITO 65.39 53.99 11.40 ENTREGUE 00063b381e2406b52ad429470734ebd5 6a899e55865de6549a58d2c6845e5604 8602a61d680a10a82cceeeda0d99ea3d 2018-07-27 14:21:27 CARTAO DE CREDITO 57.98 45.00 12.98 ENTREGUE 001021efaa8636c29475e7734483457d 2dfbf74859104caf100df3720a1d833d 6560211a19b47992c3666cc44a7e94c0 2018-02-27 06:27:14 CARTAO DE CREDITO 64.10 49.00 15.10 ENTREGUE 001dbc16dc51075e987543d23a0507c7 698a74f33469466fa4172e829505d1c6 4a3ca9315b744ce9f8e9374361493884 2017-01-28 11:17:57 CARTAO DE CREDITO 87.90 69.90 18.00 ENTREGUE 00276d5c3491fbf55305e26891040df9 54686c41e86854e35879efbd1c2cab1b 8f78f0903005064036736c7173a5c2ed 2018-02-13 09:47:21 CARTAO DE CREDITO 68.12 44.90 23.22 ENTREGUE 003423b755b562962a6225a8de40d12e 18f1bb6325d50619d5c13b7a25b869fd 23c38debaffe4a25a30fdbd9b586a13f 2018-07-08 08:28:17 BOLETO 261.33 232.75 28.58 ENTREGUE 003a94f778ef8cfd50247c8c1b582257 da108bc410acffb1400cf9caea65a332 f80edd2c5aaa505cc4b0a3b219abf4b8 2018-08-03 11:52:31 CARTAO DE CREDITO 57.98 39.90 18.08 ENTREGUE 004345d16a1ab2c21962992c721c8643 3b723b649feb48f3cfbb9c728efb3d7d 0be8ff43f22e456b4e0371b2245e4d01 2018-07-04 03:45:05 VOUCHER 53.27 37.90 15.37 ENTREGUE 0046e1d57f4c07c8c92ab26be8c3dfc0 ae55e228ded796581eccc67045516023 38e6dada03429a47197d5d584d793b41 2017-09-26 12:24:03 CARTAO DE CREDITO 15.57 7.79 7.78 ENTREGUE 004eab0fd8f28adaf8d488976f77febe c476ddfbabfa4624603e0b7f8e245057 7586919161935337bf6b6d7ff5779648 2017-08-02 12:32:46 CARTAO DE CREDITO 33.48 21.50 11.98 ENTREGUE 006e05e81c068ddc38e48ebe189b922e ebcf50ec311622a9b17a720a655a489b 6560211a19b47992c3666cc44a7e94c0 2017-12-27 19:50:43 CARTAO DE CREDITO 43.10 29.00 14.10 ENTREGUE 0084e195fbd72ae51599af47f04afede bd8d067426b640b65c68dd3ee6c71d46 bd0389da23d89b726abf911cccc54596 2018-03-14 20:57:00 CARTAO DE CREDITO 113.03 89.90 23.13 ENTREGUE 008a1b3db2a8bf63418c2cf7c7f494b1 cc2db083341ec9bb757b9f9a70b289d9 8b28d096634035667e8263d57ba3368c 2018-04-02 06:33:25 CARTAO DE CREDITO 33.12 14.89 18.23 ENTREGUE 00949655cdd8d0465e433a5e6c9643e5 141bdfe99910207edd84c00700397580 8648b1e89e9b349e32d3741b30ec737e 2018-06-25 18:14:53 BOLETO 25.87 18.00 7.87 ENTREGUE 009e11afa25aa95ae78e60a793995c9b 1b7c152aba1c7478309329cfec0bb5d1 582d4f8675b945722eda7c0cb61ba4c7 2017-10-19 21:56:16 CARTAO DE CREDITO 65.14 30.99 34.15 ENTREGUE 00a250dbdb3153cc6ecf4d3f07ef6a17 ccff27cfcda46bdff5e51b6e6711a85c cc419e0650a3c5ba77189a1882b7556a 2017-12-10 16:07:24 CARTAO DE CREDITO 61.77 53.99 7.78 ENTREGUE 00b4a910f64f24dbcac04fe54088a443 d70e5eac00a9d35a3cb193442c0287cd d50d79cb34e38265a8649c383dcffd48 2017-01-18 15:55:34 CARTAO DE CREDITO 2.54 33.99 16.60 ENTREGUE 00cfabbe2a93b70beeec4894f86712a8 bf2cd0dfd7ad8b44be636ba1079d6358 8a32e327fe2c1b3511609d81aaf9f042 2017-06-10 04:56:30 BOLETO 45.10 29.99 15.11 ENTREGUE 00dc6ad47477b3b62d3c0acbe98a82a4 5dd8298fb952a22f28534bfbda71aa2f c31eff8334d6b3047ed34bebd4d62c36 2018-02-24 16:41:24 CARTAO DE CREDITO 144.22 110.99 33.23 ENTREGUE 00e365f4fc03d1098841af23d05c17a6 491609eeefc72ee67ee5b42e63ba9859 7d13fca15225358621be4086e1eb0964 2018-08-20 06:40:45 CARTAO DE CREDITO 194.33 175.00 19.33 ENTREGUE 00f2c876aa08fbba04199823952e96c1 eb4fea182012be623175b35ee37dfe50 53e4c6e0f4312d4d2107a8c9cddf45cd 2017-04-06 07:21:23 BOLETO 86.22 69.00 17.22 ENTREGUE 0108fba93678555ad1cec9c267848187 8bbf21f65f542300bbf3ef6012820922 76d5af76d0271110f9af36c92573f765 2017-06-04 18:48:02 CARTAO DE CREDITO 219.12 199.00 20.12 ENTREGUE 010c995323bc17d8156fbe2c37fed63e eada5b345b1d846ca260ad12e8ec98cd edf96ef93ed595084bbcbd9224bd2894 2017-03-25 16:18:00 CARTAO DE CREDITO 56.12 42.00 14.12 ENTREGUE 011a43bc9bb525517251ebb3ebc99b69 bc6123686b421b9084028c34499824c4 610f72e407cdd7caaa2f8167b0163fd8 2018-04-25 15:15:05 CARTAO DE CREDITO 920.20 899.0